# Kapitel 4: Statistische Datenanalyse II – Parameterschätzung (Teil 4)

## Numerische Optimierung (optional)
Algorithmen zur numerischen Optimierung sind derzeit in vielen Bereichen von Gesellschaft und Wissenschaft im Einsatz:
- In der Physik werden **Modelle an Messdaten angepasst**, die aus physikalischen Theorien abgeleitet sind. Damit werden die Parameter des Modells oder der Theorie experimentell bestimmt.
- In der Wirtschaft werden **technische Systeme numerisch optimiert**, z. B. ist die optimale Zuordnung von Flugzeugen zu Gates am Flughafen ein interessantes Optimierungsproblem.
- Die meisten aktuellen Methoden der künstlichen Intelligenz (KI) beruhen auf **tiefem maschinellen Lernen** (engl.: deep learning). Dabei stellt das KI-Modell letztlich eine komplizierte nichtlineare Funktion der Eingabewerte dar, deren Parameter "trainiert" werden – ebenfalls ein numerisches Optimierungsproblem. Aktuelle KI-Modelle, z. B. Large Language Models, können bis zu [$10^{12}$ Parameter](https://epochai.org/data/epochdb/visualization?yAxis=Parameters) beinhalten.

Der Prozess der numerischen Optimierung benötigt folgende "Zutaten", die dem Algorithmus zur Verfügung gestellt werden müssen:
- Die **zu minimierende Funktion** wird oft als Verlustfunktion (engl.: loss function, cost function, objective function) bezeichnet. Sie ist häufig eine komplizierte Funktion, die von (potenziell vielen) Parametern abhängt, bezüglich derer sie minimiert werden soll. 
- Parameter des Algorithmus, oft **Hyperparameter** (auch: Metaparameter) genannt, wie z. B. Schrittweiten von Algorithmen oder Konvergenzkriterien.
- Möglicherweise können auch **Zwangs- oder Nebenbedingungen** (engl.: constraints) formuliert werden, z. B. Wertebereiche für Parameter.

Die Bestimmung des **globalen Minimums** einer komplizierten Funktionen ist häufig eine Herausforderung für Optimierungsalgorithmen. Die Algorithmen, die dazu zum Einsatz kommen, besitzen häufig Mechanismen um zu verhindern, dass die Minimierung in einem lokalen Minimum "steckenbleibt".

### Verfahren zur Funktionsminimierung
Verfahren zur Funktionsminimierung lassen sich grob in drei Klassen einteilen. Die ersten beiden Verfahren beruhen auf der Suche nach Minima durch Auswertung der Funktion an Stützpunkten:
- Bei der **Rastersuche** (engl.: grid search) wird die Verlustfunktion auf einem festen Raster von Stützpunkten ausgewertet und der minimale Funktionswert gesucht. Da die Funktion a priori nicht bekannt ist, werden häufig Stützpunkt mit gleichem Abstand verwendet. Diese Klasse von Verfahren skaliert nicht gut mit hochdimensionalen Funktionen: mit $k$ Stützpunkten pro Dimension sind für $d$ Dimensionen $k^d$ Funktionsauswertungen nötig. Eine Möglichkeit das Verfahren zu verbessern ist ein angepasstes Raster mit engeren Abständen dort, wo sich die Funktion stark ändert.
- Eine **Monte-Carlo-Suche** wertet die Verlustfunktion an zufällig verteilten Stützpunkten aus. Dieses Verfahren ist verwandt mit der Monte-Carlo-Integration. Wie alle Monte-Carlo-Verfahren ist dies besonders für hochdimensionale Funktionen effizienter als eine Rastersuche. Die "Kunst" besteht darin, die Stützpunkte geschickt zu verteilen. Wie bei der Rastersuche sollten mehr zufällige Stützpunkte dort generiert werden, wo sich die Funktion stark ändert.

Die dritte Klasse beinhaltet **numerische Optimierungsverfahren** und lässt sich weiter unterteilen in
- **Direkte Suchverfahren**, die mit einer gut motivierten aber einfachen und robusten Regel zur Funktionsauswertung Schritt für Schritt zum Minimum vorstoßen, und
- Iterative **Abstiegsverfahren**, die auf der ersten und/oder zweiten Ableitung der Funktion beruhen und mithilfe dieser Ableitungen den Weg zum Minimum finden.
    
In SciPy sind eine Reihe von gängigen Verfahren zur Funktionsminimierung in `scipy.optimize.minize()` implementiert.

### Rosenbrockfunktion
Eine häufig verwendete Beispielfunktion zum Test von Optimierungsverfahren ist die **Rosenbrockfunktion**, manchmal auch als "Bananenfunktion" bezeichnet:
$$
f(x,y) = (a-x)^2 + b( y-x^2)^2.
$$
Für die Parameterwahl $a=1$ und $b=100$ besitzt diese Funktion ein globales Minimum bei $(x,y)=(1,1)$. Um dieses Minimum herum liegt allerdings ein flaches Tal entlang der Bananenform, das für Optimierungsverfahren eine Herausforderung darstellt. Die Rosenbrockfunktion und ihr Minimum werden mit dieser Parameterwahl in folgendem Codebeispiel mit `scipy.optimize.rosen` aufgetragen:

In [ ]:
"""Rosenbrock function: standard example of numerical optimization"""

import numpy as np
import matplotlib
import matplotlib.pyplot as plt

x = np.linspace( -1.5, 1.5, 300 )
y = np.linspace( -1, 2, 300 )
X, Y = np.meshgrid( x, y )

rosen = lambda x, y: ( 1 - x )**2 + 100*( y - x**2 )**2
Z = rosen( X, Y )
levels = np.logspace( -2, 3, 16 )

fig, ax = plt.subplots()
CS = ax.contourf( X, Y, Z, levels, cmap=matplotlib.cm.gray, norm=matplotlib.colors.LogNorm() )
fig.colorbar( CS, ax=ax )
ax.plot( 1, 1, marker="o", color="orange" )
ax.set_xlabel( r'$x$' )
ax.set_ylabel( r'$y$' )

plt.show()

### Simplexverfahren
Das **Simplexverfahren** (John Nelder, Roger Mead, 1965) ist ein **heuristisches Verfahren** zur direkten Suche nach Funktionsminima. Mit **Heuristik** werden praktische Methoden bezeichnet, die eine Aufgabe (hier die Minimumssuche) mit begrenzten Informationen zufriedenstellend löst. Die Heuristik des Simplexverfahrens beruht auf einem geometrischen Objekt, das als **Simplex** bezeichnet wird. In zwei Dimensionen ist der Simplex ein Dreieck. Dieses Konzept kann aber auch auf $d$ Dimensionen erweitert werden. Dann ist der Simplex ein $d$-dimensionaler Polyeder, der aus $d+1$ Punkten besteht. Der Algorithmus von Nelder und Mead beruht auf der Idee, den Simplex systematisch zu verändern, so dass er auf das Minimum einer Funktion zuläuft. Dazu wird in jedem Schritt der Punkt auf dem Simplex durch einen besseren Punkt zu ersetzen, der den "schlechtesten" Funktionswert besitzt. Dazu kann der Simplex an den anderen Punkten gespiegelt werden, er kann in eine Richt expandiert oder kontrahiert werden oder insgesamt geschrumpft werden. Das Verfahren ist sehr robust, denn es benötigt nur Funktionswerte, keine Ableitungen. Es ist andererseits aber häufig ineffizient, braucht also verhältnismäßig lang, um auf das Minimum zu konvergieren. Außerdem besteht die Gefahr der Konvergenz auf ein lokales Minimum. Die folgende Animation illustriert das Verfahren (Quelle: Nicoguaro, [Nelder-Mead_Rosenbrock.gif](https://commons.wikimedia.org/w/index.php?title=File:Nelder-Mead_Rosenbrock.gif&oldid=260874010), CC BY 4.0, dort findet sich auch der zugehörige Python-Code):

<img src="img/Nelder-Mead_Rosenbrock.gif" width=50%>


>**Nelder-Mead-Algorithmus im Detail**
>
>Der Nelder-Mead-Algorithmus soll die Funktion $f(\mathbf{x})$ minimieren. Der Simplex besteht aus $n+1$ Punkten $\mathbf{x}_i$ in $\mathbb{R}^n$. Der Algorithmus besteht aus folgenden Schritten:
>
>**Schritt 1**: **Sortiere** $\mathbf{x}_i$ nach ansteigenden Funktionswerten $f(\mathbf{x}_i)$, teste **Abbruchbedingung** (z. B. feste Anzahl von Schritten, Größe des Simplex)
>
>**Schritt 2**: Berechne **Schwerpunkt** der ersten $n$ Punkte $\mathbf{x}_1, \dots, \mathbf{x}_n$: 
>$$
\mathbf{x}_S = \frac{1}{n}\sum_{i=1}^n \mathbf{x}_i.
>$$
>
>**Schritt 3**: **Spiegele** $\mathbf{x}_{n+1}$ an $\mathbf{x}_S$: 
>$$
\mathbf{x}_r = \mathbf{x}_S + \alpha( \mathbf{x}_S - \mathbf{x}_{n+1} ).
>$$ 
>Dabei wird der Hyperparameter $\alpha > 0$ als Reflexionsparameter bezeichnet (z. B. $\alpha=1$). 
>
>$\to$ falls $f(\mathbf{x}_1) < f(\mathbf{x}_r) < f(\mathbf{x}_n)$: ersetze $\mathbf{x}_{n+1}$  durch $\mathbf{x}_r$ und gehe zu Schritt 1.
>
>**Schritt 4**: Falls $f(\mathbf{x}_r) < f(\mathbf{x}_1)$: **expandiere** Simplex, 
>$$
\mathbf{x}_e = \mathbf{x}_S + \gamma( \mathbf{x}_r - \mathbf{x}_S ),
>$$ 
> wobei der Hyperparameter $\gamma > 1$ Expansionsparameter heißt (z. B. $\gamma = 2$). 
>
>$\to$ falls $f(\mathbf{x}_e) < f(\mathbf{x}_r)$: ersetze $\mathbf{x}_{n+1}$ durch $\mathbf{x}_e$, ansonsten durch $\mathbf{x}_r$, und gehe zu Schritt 1.
>
>**Schritt 5**: Nun gilt $f(\mathbf{x}_r) > f(\mathbf{x}_n)$: **kontrahiere** Simplex, 
>$$
\mathbf{x}_c = \mathbf{x}_S + \rho( \mathbf{x}_{n+1} - \mathbf{x}_S ), 
>$$
> mit dem Hyperparameter $0 < \rho < 1$ "Kontraktionssparameter" (z. B. $\rho = 0.5$). 
>
>$\to$ falls $f(\mathbf{x}_c) < f(\mathbf{x}_{n+1})$: ersetze $\mathbf{x}_{n+1}$ durch $\mathbf{x}_c$ und gehe zu Schritt 1.
>
>**Schritt 6**: **Schrumpfe** Simplex durch Ersetzung 
>$$
\mathbf{x}_i = \mathbf{x}_1 + \sigma( \mathbf{x}_{i} - \mathbf{x}_1 )
>$$ 
>für alle $i > 1$ mit dem Hyperparameter $0 < \sigma < 1$ "Schrumpfungsparameter" (z. B. $\sigma=0.5$) und gehe zu Schritt 1. 

### Gradientenverfahren
Das **Gradientenverfahren** (engl.: gradient descent, steepest descent) ist Beispiel für die Klasse der **Abstiegsverfahren**. Die grundlegende Idee aller dieser Verfahren besteht darin, die Abstiegsrichtung $\mathbf{d}_i$ der Verlustfunktion $f(\mathsf{x})$ am Punkt $\mathbf{x}_i$ zu finden. Der nächste Punkt $\mathbf{x}_{i+1}$ wird dann durch einen Schritt in diese Richtung erreicht: $\mathbf{x}_{i+1} = \mathbf{x}_i + t_i \mathbf{d}_i$. Der Hyperparameter $t_i$ gibt die **Schrittweite** vor, im Bereich des maschinellen Lernens wird er auch oft als **Lernrate** (engl.: learning rate) bezeichnet. Dieser Abstieg entlang der Abstiegsrichtung wird so lange durchgeführt, bis ein Abbruchkriterium erfüllt ist.

Das Gradientenverfahren verwendet für die Abstiegsrichtung die **Richtung des steilsten Abstiegs**, mathematisch also den negativen Gradienten: 
$$
\mathbf{d}_i = -\nabla f(\mathbf{x_i}).
$$
Das Verfahren benötigt also die erste Ableitung der Funktion und wird daher als Algorithmus erster Ordnung bezeichnet. Es ist in der folgenden Abbildung anhand der Rosenbrockfunktion illustriert. Die Pfeile sind die einzelnen Schritte, jeweils in Richtung des größten negativen Gradienten am Startpunkt:

<img src="img/gradient_descent.png" width=40%>

Beim Gradientenverfahren besteht die "Kunst" darin, die Schrittweite so zu wählen, dass $f(\mathbf{x}_i)$ möglichst schnell kleiner wird und so das Minimum in möglichst wenigen Schritten erreicht wird. Eine zu kleine Schrittweite führt zu sehr vielen Schritten und damit zu langsamer Konvergenz. Sie birgt außerdem die Gefahr, in lokalen Minima "stecken zu bleiben". Mit einer zu großen Schrittweite könnte der Algorithmus "über das Minimum hinausschießen", was wiederum zu langsamer Konvergenz führt. Moderne Optimierungsalgorithmen wie [Adam](https://arxiv.org/abs/1412.6980) verwenden daher zusätzlich stochastische Elemente (Auswertung nur auf einem Teil der Daten) und/oder lehnen sich an physikalische Konzepte wie den Impuls an.

## Ausblick: Moderne Methoden der Datenanalyse
Der Kurs Computergestützte Datenauswertung gibt nur einen ersten Einblick in die Auswertung von Daten mit dem Computer. In Wissenschaft und Wirtschaft sind viele weitere und tiefergehende Methoden und Algorithmen im Einsatz. Dazu gehören unter anderem:
- die **Maximum-Likihood-Methode** als Grundlage vieler moderner Methoden der Datenanalyse,
- aufwändigere Methoden der **Modellanpassung**, z. B. mit Zwangs- und/oder Nebenbedingungen ,
- **Intervallschätzung** im Rahmen der frequentistischen Statistik (Konfidenzintervalle) oder der bayesschen Statistik (Glaubwürdigkeitsintervalle),
- **Hypothesentests** und statistische Klassifizierung,
- **Maschinelles Lernen** als aktuelles Kerngebiet der künstlichen Intelligenz (KI).

Im Physikstudium am KIT werden Sie mit solchen Methoden in vielen Forschungsfeldern in Berührung kommen insbesondere in der Teilchen- und Astroteilchenphysik. Im 5. Fachsemester des Bachelorstudiengangs Physik wird ein **Wahlpflichtkurs zur Datenanalyse** angeboten, der weitere Grundlagen zu eine Bachelorarbeit in der Datenanalyse legt. Teil des Kurrikulums im Masterstudiengang Physics am KIT ist der Kurs "Modern Methods of Data Analysis", der fortgeschrittene Themen aus dem Bereich der "Data Science" behandelt.

### Maximum-Likelihood-Methode
#### Übersicht
Die **Maximum-Likelihood-(ML-)Methode** wurde von Ronald Aylmer Fisher um das Jahr 1912 eingeführt. Wie in der Methode der kleinsten  (LS-Methode) beruht in der ML-Methode die Parameterschätzung auf der Suche nach Extremwerten einer Funktion, so dass ein statistisches Modell mit freien Parametern am besten "zu den Daten passt". Diese Funktion heißt **Likelihood-Funktion** und ihre Maximierung führt auf Schätzwerte für diese Parameter. Im Gegensatz zur LS-Methode, die nur unter bestimmten Voraussetzungen gut funktioniert, ist die ML-Methode universell einsetzbar und die Basis vieler fortgeschrittener statistischer Methoden wie z. B. Hypothesentests. Die ML-Methode besitzt eine Reihe "guter Eigenschaften": sie ist u. a. **effizient**, d. h. sie liefert die kleinstmögliche Varianz des Schätzwerts und somit die geringstmögliche Unsicherheit. Für Zufallsvariablen, die einer Normalverteilung folgen, sind **LS-Methode und ML-Methode äquivalent**, sie liefern also dieselben Schätzwerte für Größen wie Erwartungswert und Varianz einer Verteilung.

>**Exkurs: Eigenschaften von Schätzwerten**
>
>Im folgenden soll kurz in Worten beschrieben werden, welche Eigenschaften von Schätzwerten als besonders günstig angesehen werden. Für (fast) alle dieser Eigenschaft gibt es auch eine mathematische Formulierung, die in fortgeschrittenen Kursen und in der statistischen Fachliteratur diskutiert wird. Zu diesen Eigenschaften gehören:
>- **Erwartungstreue**: ein Schätzwert wird als erwartungstreu (engl.: unbiased) bezeichnet, wenn er keine (oder nur eine geringe) **Verzerrung** (engl.: bias) besitzt. Als Verzerrung wird die Abweichung des erwarteten Schätzwerts von wahrem Wert bezeichnet. Das arithmetische Mittel, das sich sowohl in der LS- als auch in der ML-Methode als Schätzwert für den Erwartungswert ergibt, ist erwartungstreu. Dahingegen ist der Schätzwert der LS- und ML-Methode für die Varianz ein Beispiel für einen verzerrten Schätzwert. Erst mit der Besselkorrektur ergibt sich ein erwartungstreuer Schätzwert, die Stichprobenvarianz.
>- **Konsistenz**: ein Schätzwert heißt konsistent, wenn er im Grenzfall großer Stichproben gegen den wahren Wert konvergiert. Die Stichprobenvarianz ohne Besselkorrektur ist für kleine Stichproben verzerrt, konvergiert aber für große Stichproben gegen den wahren Wert. Sie ist also nicht erwartungstreu, aber konsistent.
>- **Effizienz**: ein Schätzwert wird als effizient bezeichnet, wenn er die kleinstmögliche Varianz besitzt. Effiziente Schätzwerte können also mit der geringstmöglichen Unsicherheit bestimmt werden. In der statistischen Literatur wird dies unter dem Stichwort [Cramér-Rao-Ungleichung](https://de.wikipedia.org/wiki/Cramér-Rao-Ungleichung) diskutiert. Effiziente Schätzwerte sind einer der großen Vorteile der ML-Methode.
>- **Genauigkeit**: die Genauigkeit eines Schätzwerts bemisst sich an seiner mittleren quadratischen Abweichung (engl.: mean squared error, MSE), definiert als die Summe aus Varianz und Quadrat der Verzerrung. Große Genauigkeit entspricht einem kleinen MSE und ist eine Kombination aus kleiner Varianz und kleiner Verzerrung.
>- **Robustheit**: ein robuster Schätzwert ist wenig empfindlich auf "Ausreißer" in Daten oder ein fehlerhaftes Modell. Beispielsweise ist das arithmetische Mittel als LS- und ML-Schätzwert für den Erwartungswert anfällig gegen Ausreißer, wohingegen der Median deutlich robuster ist.
>- **Einfachheit**: oft muss eine einfache Definition eines Schätzwerts, und damit häufig eine einfache Implementation in Computercode, gegen andere Kriterien wie Erwartungstreue abgewogen werden.

Die unterschiedlichen Ansätze der LS-Methode und der ML-Methode zur Lösung der Frage "welche Modellparameter passen am besten zu den Daten?" sollen nun verglichen werden:
- Die **LS-Methode** minimiert die Summe der Residuenquadrate, d. h. den Abstand der Datenpunkte $y_i$ vom Erwartungswert der Modellfunktion $\lambda_i$, normiert auf die Varianz $\sigma_i^2$:
    $$
    S \equiv\chi^2\equiv \sum_i \frac{(y_i-\lambda_i)^2}{\sigma_i^2} \overset{!}{=}\mathsf{min}
    $$
    und nur diese beiden Größen müssen bekannt sein.
- Die **ML-Methode** maximiert, wie unten genauer eingeführt wird, den Funktionswert der Wahrscheinlichkeitsdichtefunktion (PDF) am Ort der Messung. Dazu muss die gesamte PDF bekannt sein, nicht nur Erwartungswert und Varianz.

Dieser Unterschied im Ansatz ist in folgendem Codebeispiel illustriert. Als Modellfunktion dient eine Normalverteilung, sie ist für drei unterschiedliche Parametersätze abgebildet. Die Messung (roter Pfeil) wird im Rahmen der LS- und der ML-Methode verglichen. Für Normalverteilungen sind beide Methoden äquivalent – dies wird weiter unten gezeigt, sie verfolgen aber einen anderen Ansatz. Die LS-Methode bestimmt den **quadratischen Abstand vom Erwartungswert** (gestrichelte Linie) und normiert ihn auf die Varianz (nicht gezeigt). Die ML-Methode wertet den **Funktionswert der PDF** (gepunktete Linie) beim Messwert aus.

In [ ]:
"""Illustrate difference of least squares methode and maximum likelihood method"""
import numpy as np
import matplotlib.pyplot as plt
from scipy.stats import norm

x = np.linspace( -5, 5, 200 )
xm = 1.75
mu  = [0,0,1]
sig = [1,2,1]   

fig, ax = plt.subplots( 1, 3, figsize=(15,4) )

# plot PDFs with different model parameters
for l, s, a in zip( mu, sig, ax ):
    # plot curve
    line, = a.plot( x, norm.pdf( x, loc=l, scale=s ), label=r"$\mu=%d, \sigma=%d$" % ( l, s )  )

    # annotate
    pdfl = norm.pdf( l, loc=l, scale=s )    
    pdfm = norm.pdf( xm, loc=l, scale=s )
    a.vlines( l, 0, pdfl, linestyles="dashed", colors=line.get_color() )
    a.hlines( pdfm, -3.5, 3.5, linestyles="dotted", colors=line.get_color() )
    a.arrow( xm, 1.2*pdfm, 0, -1.2*pdfm, head_width=0.15, head_length=0.02, length_includes_head=True, color="r" )
    a.text( xm - 0.1, 1.2*pdfm+0.01, "Measurement", color="r" )
    a.annotate( "", xy=(l, 0.05), xytext=(xm,0.05), arrowprops=dict(arrowstyle="<->",linestyle="dashed",color=line.get_color()) )
    a.annotate( "", xy=(-3, 0), xytext=(-3,pdfm), arrowprops=dict(arrowstyle="<->",linestyle="dotted",color=line.get_color()) )
               
    a.set_xlabel( "$x$")
    a.set_ylabel( "Probability Density Function" )
    a.set_ylim( 0, 0.45 )
    a.legend()

plt.show()

>**Bemerkung:** Mit der gewöhnlichen LS-Methode, also ohne die Normierung auf die Varianz, wären die ersten beiden Fälle nicht zu unterscheiden.

#### Likelihood-Funktion

Die zentrale Größe, die innerhalb der Maximum-Likelihood-Methode zur Parameterschätzung verwendet wird, ist die **Likelihood-Funktion** $L$. Um sie zu konstruieren muss für Messwerte $\mathbf{x}\equiv(x_1,\dots,x_n)^\mathsf{T}$ aus einer Stichprobe der Größe $n$ die PDF $f(x;\mathbf{a})$ bekannt sein. Dabei ist $f$ eine PDF im Wahrscheinlichkeitsraum der Zufallsvariablen $x$ (siehe Kapitel 2) und ist in diesem Raum auf Eins normiert,
$$
\int f(x;\mathbf{a})\,\mathsf{d}x = 1.
$$

Die PDF hängt von $m$ Parametern $\mathbf{a}\equiv(a_1,\dots,a_m)^\mathsf{T}$ ab. Die **Likelihood-Funktion** ist definiert als das **Produkt der Wahrscheinlichkeitsdichten** aller Messungen:
$$
L(\mathbf{a}) \equiv L(\mathbf{a}|\mathbf{x}) 
\equiv \prod\limits_{i=1}^n f(x_i;\mathbf{a}).
$$
Die Likelihood-Funktion nimmt umso größere Werte an, desto besser die Parameter $\mathbf{a}$ zu den Daten "passen". Die Schreibweise $L(\mathbf{a})$ bzw. $L(\mathbf{a}|\mathbf{x})$ soll andeutet, dass die Likelihood-Funktion eine **Funktion der Parameter** ist, also im Parameterraum "lebt". $L$ wird also *nach* der Messung ausgewertet, d. h. die $x_i$ **liegen fest** und wurden bereits in $L$ eingesetzt. Genauso hatten wir auch die Summe der Residuenquadrate $S\equiv\chi^2$ für die LS-Methoden als Funktion von $\mathbf{a}$ interpretiert. Beachten Sie, dass $L$ **keine PDF in Parameterraum** und entsprechend auch nicht auf Eins normiert ist. 

#### Maximum-Likelihood-Prinzip
Mithilfe der Likelihood-Funktion lässt sich jetzt das Prinzip der ML-Methode zur Parameterschätzung formulieren:

>**Maximum-Likelihood-Prinzip**: Der Maximum-Likelihood-Schätzwert $\hat{\mathbf{a}}$ für einen Parametervektor $\mathbf{a}$ ist derjenige Wert von $\mathbf{a}$, für den die Likelihood-Funktion den größten Wert annimmt: 
>$$
L(\hat{\mathbf{a}}) \geq L(\mathbf{a}) \quad\forall \mathbf{a}.
>$$

Das Maximum-Likelihood-Prinzip beinhaltet also die **Maximierung** der Likelihood-Funktion $L$. In der Praxis wird allerdings fast immer der **negative Logarithmus** von $L$ (engl.: negative log likelihood, NLL) **minimiert**:
$$
-\ln L(\mathbf{a}) \overset{!}{=}\mathsf{min}
$$
Da der Logarithmus eine streng monotone Funktion ist, besitzt $-\ln L(\mathbf{a})$ genau dort ein Minimum, wo $L(\mathbf{a})$ ein Maximum besitzt. Die notwendige Bedingung für den Schätzwert $\hat{\mathbf{a}}$ ist damit
$$
\frac{\partial (-\ln L(\mathbf{a}))}{\partial a_j} \overset{!}{=} 0 \quad\forall j.
$$
Die hinreichende Bedingung für ein Minimum bei $\hat{\mathbf{a}}$ ist, dass die Matrix der zweiten partiellen Ableitungen (Hesse-Matrix)
$$
\left.\frac{\partial^2 (-\ln L(\mathbf{a}))}{\partial a_i\,\partial a_j}\right|_{\mathbf{a} = \mathbf{\hat a}}
$$
positiv definit (d. h. die Hesse-Matrix von $L(\mathbf{a})$ negativ definit), die negative Log-Likelihood-Funktion also eine konvexe Funktion ist. Die Minimierung von $-\ln L(\mathbf{a})$ ist in wenigen Fällen analytisch möglich, in den meisten Fällen wird sie allerdings numerisch durchgeführt.

Die Verwendung von $-\ln L(\mathbf{a})$ bietet sich aus folgenden Gründen an:
- Durch das Bilden des Logarithmus werden aus Produkten Summen:
    $$
    -\ln L(\mathbf{a}) = -\sum_{i=1}^n f(x_i;\mathbf{a}).
    $$
- Beim Logarithmieren werden aus konstanten Faktoren konstante Summanden. Für das Minimum einer Summe spielen diese konstanten Summanden keine Rolle: sie verschieben alle Funktionswerte nach oben oder unten und fallen beim Bilden der Ableitung weg und können daher in der numerischen Minimierung weggelassen werden. Das spart häufig Rechenzeit, z. B. wenn Fakultäten auftreten wie in der Poisson-PDF (Kapitel 2).
- Für eine numerische Auswertung der Likelihood-Funktion ist es hilfreich, dass  der Logarithmus von $L$ numerisch viel kleiner ist als $L$ selbst. Es ist nicht ungewöhnlich, dass $L$ numerisch sehr groß wird und damit die numerische Genauigkeit der Gleitkommadarstellung im Computer an ihre Grenzen stößt. Für eine 32-Bit-Gleitkommazahl ist der größte darstellbare Wert $3.4028235\times 10^{38}$. Der natürliche Logarithmus dieser Zahl ist 88.7228, dieser Wert ist mit Gleitkommazahlen viel besser darstellbar.

Im folgende Codebeispiel werden die Datenpunkte und die daraus berechnete negative Log-Likelihood-Funktion für $n=1$ bis $n=5$ normalverteilte Zufallszahlen mit Lokalisierungsparameter $\mu=5$ und Skalierungsparameter $\sigma=1$ grafisch dargestellt. Analog zur LS-Methode ergibt sich eine Parabel um den Schätzwert $\hat{\mu}$, die mit Hinzunahme von Zufallszahlen immer stärker gekrümmt ist. In den Abbildung der unteren Zeile ist jeweils $\Delta(-\ln L(\mu))$ dargestellt, definiert also der Abstand der negativen Log-Likelihood-Funktion von ihrem Minimalwert $-\ln L(\hat\mu)$.

In [ ]:
"""Maximum likelihood method: negative log likelihood for more and more data"""

import numpy as np
import matplotlib.pyplot as plt
import matplotlib.animation as anim

# construct negative log likelihood function for Gaussian
def NLL_gaussian( mu, sigma, data ):

    sig2 = sigma**2

    # constant terms ignored as they are irrelevant for the function's minimum
    #N = len( data )
    #const = 0.5 * N * ( np.log(2*np.pi) + np.log( sig2 ) )

    # construct negative log likelihood the Python/NumPy way
    DATA, MU = np.meshgrid( data, mu )
    return np.sum( 0.5*(DATA-MU)**2/sig2, axis=1 )

    # this is equivalent to, but less readable than, the following
    #NLL = 0
    #for i in np.arange( N ):
    #    NLL += 0.5*(data[i]-mu)**2/sig2
    # return NLL

# true model parameters
atrue = 5
sig   = 1

# data points
n = 5
steps = 500
xi = np.linspace( 1, n, n )
xrange = np.linspace( 0.5, n + 0.5, steps )

# scan of a values
mumin, mumax = 0., 10.
mu = np.linspace( mumin, mumax, steps )

rng = np.random.default_rng( 42 )
yi = rng.normal( loc=atrue, scale=sig, size=n )

fig,ax = plt.subplots( 2, 5, figsize=(25,10) )

for i in np.arange( len(yi) ):
    # compute NLL for first i data points
    NLL = NLL_gaussian( mu, sig, yi[:i+1] )

    NLL_min = np.amin( NLL )
    muhat = np.mean( yi[:i+1] ) # using our knowledge that the ML estimator is the mean

    # plot data points
    ax[0][i].errorbar( xi[:i+1], yi[:i+1], yerr=sig, fmt="ro" )
    ax[0][i].set_xlabel( r"$x$")
    ax[0][i].set_ylabel( r"$y$")
    ax[0][i].set_xlim( 0, 6 )
    ax[0][i].set_ylim( 0, 8 )
    ymean = np.repeat( muhat, steps )
    ax[0][i].plot( xrange, ymean, "r--" )

    # plot NLL
    ax[1][i].set_title( r"%d random number(s): $\hat{\mu} = %4.3f$" % ( i+1, muhat ) )
    ax[1][i].plot( mu, NLL-NLL_min )
    ax[1][i].set_xlabel( r"$\mu$")
    ax[1][i].set_ylabel( r"$\Delta(-\ln L(\mu))$")
    ax[1][i].set_xlim( 0, 10 )
    ax[1][i].set_ylim( 0, 50 )

plt.show()

#### Maximum Likelihood: analytische Lösung
Für eine **Normalverteilung** lässt sich die Likelihood-Funktion **analytisch** minimieren. Damit lässt sich gleichzeitig die Äquivalenz von ML-Methode und LS-Methode für Normalverteilungen zeigen. Wir schreiben die Likelihood-Funktion explizit als
$$
L(\mu,\sigma) = \prod\limits_{i=1}^{n} \frac{1}{\sqrt{2\pi}\,\sigma}
\exp\left[
-\frac{(x_i - \mu)^2}{2\sigma^2}
\right].
$$
Zur Erinnerung: $L$ ist eine Funktion der Parameter $\mu$ und $\sigma$, nicht der Daten. Der negative natürliche Logarithmus dieser Likelihood-Funktion (NLL) Ausdrucks ergibt sich dann als
$$
-\ln L(\mu,\sigma) = \frac{1}{2} \sum\limits_{i=1}^{n} 
\left[
\ln(2\pi) + \ln(\sigma^2) + \frac{(x_i - \mu)^2}{\sigma^2}
\right],
$$
wobei die Rechenregel für den Logarithmus $\ln x^a$ = $a\ln x$ verwendet wurde. Die konstanten Summanden $1/2 \cdot n \cdot (\ln(2\pi) + \ln(\sigma^2) )$ sind irrelevant für das Minimum und können weggelassen werden. Die verbleibenden Summanden beschreiben eine Parabel im Parameter $\mu$. Der Vergleich mit der Summe der Residuenquadrate
$$
S = \sum_{i=1}^{n} \frac{(x_i - \mu)^2}{\sigma_i^2}
$$
zeigt, dass beide Größen für den Fall, dass die $x_i$ alle aus derselben PDF stammen und somit dieselbe Varianz $\sigma_i^2\equiv\sigma^2$ besitzen, bis auf einen Faktor 1/2 und die oben genannten konstanten Summanden gleich sind:
$$
-\ln L = \frac{1}{2} S + \mathsf{const}.
$$
Beide besitzen für eine Normalverteilung dasselbe Minimum, das wir bereits am Anfang von Kapitel 4 analytisch ausgerechnen haben, und liefern demnach **denselben Schätzwert**. Für andere Verteilungen sind die **ML-Methode und die LS-Methode im allgemeinen nicht äquivalent**.

Auch für die **Poissonverteilung** kann die Minimierung der NLL analytisch durchgeführt werden. Die NLL ergibt sich aus der Poisson-PDF als
$$
\begin{split}
L(\nu) &= \prod\limits_{i=1}^N \frac{\nu^{n_i}}{n_i!}\exp[-\nu]\\
-\ln L(\nu) &= \sum\limits_{i=1}^N 
\left[
-n_i \ln\nu + \ln(n_i!) + \nu
\right] \\
&=N\nu - \sum\limits_{i=1}^N n_i \ln\nu + \textsf{const}.
\end{split}
$$
Das Minimum der NLL ergibt sich aus folgender kurzer Rechnung:
$$
\begin{split}
\frac{\partial \ln (-L(\nu))}{\partial \nu} &=
N - \sum\limits_{i=1}^N\frac{n_i}{\nu} \overset{!}{=} 0\\
\quad\to\quad
\hat\nu &= \frac{1}{N}\sum\limits_{i=1}^N n_i.
\end{split}
$$
Es ergibt sich wieder das arithmethische Mittel der Messwerte als ML-Schätzwert für den Erwartungswert. Der konstante Term fällt bei der Minimierung weg. Dies ist numerisch von Vorteil, denn dieser Term enthält Fakultäten von möglicherweise großen Zahlen. 

#### Varianz von Maximum-Likelihood-Schätzwerten
Auch die von der LS-Methode bereits bekannte **grafische Methode** zur Bestimmung der Varianz funktioniert ganz ähnlich für die ML-Methode, auch für nicht normalverteilte Zufallsvariablen. Die Idee ist wieder, die negative Log-Likelihood-Funktion um ihr Minimum bis zum quadratischen Term zu entwickeln:
$$
-\ln L(a) \approx
-\ln L(\hat{a})
+ \left.\frac{\partial(-\ln L(a))}{\partial{a}}\right|_{a = \hat{a}}
(a - \hat{a})
+ \frac{1}{2} \left.\frac{\partial^2(-\ln L(a))}{\partial a^2}\right|_{a = \hat{a}}
(a - \hat{a})^2.
$$
Die erste Ableitung verschwindet wieder am Minimum und für die zweite Ableitung kann wieder ein Zusammenhang mit der Inversen der Varianz $\mathsf{V}[\hat{a}]^{-1}$ hergestellt werden. Dieser ist allerdings nicht mehr so einfach aus einer linearen Fortpflanzung der Unsicherheit zu gewinnen, sondern muss über die oben schon erwähnte Cramér-Rao-Ungleichung gezeigt werden – dies wird in fortgeschrittenen Lehrbüchern und Vorlesungen zur statistischen Datenanalyse besprochen. Näherungsweise ergibt sich, dass das Intervall $\hat{a}\pm\sqrt{\mathsf{V}[\hat{a}]}\equiv\hat{a}\pm\sigma_{\hat{a}}$ gegeben ist durch
$$
\begin{split}
-\ln L(a) &\approx -\ln L(\hat{a}) + \frac{1}{2} \\
\quad\to\quad
\Delta(-\ln L(a)) &\equiv -\ln L(a) - (- \ln L(\hat a)) \approx \frac{1}{2}.
\end{split}
$$
Die Unsicherheit der Parameterschätzung kann also durch einen Scan der negativen Log-Likelihood-Funktion für den Funktionswert $-\ln L(\hat a) + 1/2$ gewonnen werden, eine horizontale Linie im vertikalen Abstand von 1/2 vom Minimum. Manchmal wird auch $-2\ln L(\hat a)$ aufgetragen, dann beträgt der Abstand der horizontalen Linie vom Minimum Eins. Das folgende Codebeispiel illustriert das für eine Poissonverteilung. Für dieser Verteilung ist die negative Log-Likelihood-Funktion keine Parabel:


In [ ]:
""" Variance of ML estimators (example: Poisson)"""

import numpy as np
import matplotlib.pyplot as plt

def NLL_poisson( nu, data ):
    """construct negative log likelihood function for Poisson distribution"""
    
    N = len( data )
    ln_nu = np.log( nu )

    # constant terms ignored as they are irrelevant for the function's minimum

    # const = sum ln n! 

    # construct negative log likelihood the Python/NumPy way
    DATA, LN_NU = np.meshgrid( data, ln_nu )
    return N * nu - np.sum( DATA * LN_NU, axis=1 )

    # this is equivalent to, but less readable than, the following
    # NLL = N * nu
    #for i in np.arange( N ):
    #    NLL -= data[i] * ln_nu 
    #return NLL

# function for equivalent parabola (using second derivative at minimum)
def NLL_parabola( x, xmin, ymin, ddymin ):
    return ymin + 0.5*ddymin*(x-xmin)**2

# Data: 5 Poisson distributed data points
npoints = 5
nu = 5

x,dx = np.linspace( 1, 11, 1000, retstep=True )
rng = np.random.default_rng()
data = rng.poisson( nu, npoints )

# NLL for first datapoint
fig,ax = plt.subplots()
xmin = np.mean( data )
imin = np.searchsorted( x, xmin, side='left' )

# NLL minus value at minimum
y    = NLL_poisson( x, data ) - NLL_poisson( xmin, data )

# numerical derivative through difference quotient
dy  = np.gradient( y, dx )
ddy = np.gradient( dy, dx )

# graphical solution: find interval by identifying points where NLL - NLL(min) = 0.5 
# technique: using indexes in sorted arrays left and right of the minimum
ilo = np.searchsorted( -y[:imin], -0.5, side='left' )
ihi = imin + np.searchsorted( y[imin:], 0.5, side='right' )

# comparison with parabola using second derivative at minimum
sigma = 1./np.sqrt(ddy[imin])
plot = ax.plot( x, NLL_parabola(x, x[imin], 0, ddy[imin] ), '--', label="2nd derivative:\t\t" + r"$%4.2f \pm %4.2f$" % ( x[imin], sigma ) )
ax.vlines( [x[imin], x[imin]-sigma, x[imin]+sigma], 0, 1.25, plot[-1].get_color(), 'dotted' )

plot = ax.plot( x, y, label="graphical solution:\t" + r"$%4.2f^{+%4.2f}_{-%4.2f}$" % ( x[imin], x[ihi] - x[imin], x[imin] - x[ilo] ) )
ax.hlines( 0.5, 0, 10, plot[-1].get_color(), 'dotted' )
ax.vlines( [x[ilo], x[ihi]], 0, 1.25, plot[-1].get_color(), 'dotted' )

ax.set_xlabel( r'$\nu$' )
ax.set_ylabel( r'$\Delta(-\ln L(\nu))$' )
ax.set_xlim( xmin-2, xmin+2 )
ax.set_ylim(0,2)
ax.legend()

plt.show()


### Hypothesentests
Eine der wichtigsten Fragen an Daten ist, ob sie (wissenschaftliche, politische, ...) Hypothesen unterstützen oder ob Hypothesen aufgrund der Daten verworfen werden müssen. In der Statistik gibt es dazu klar definierte **quantitative Testverfahren**, die als **Hypothesentests** bezeichnet werden. Die grundsätzliche Aufgabenstellung dabei ist, eine Stichprobe aus Daten mit einer oder mehreren Hypothesen $H_i$ zu vergleichen und die Fragen zu beantworten:
- Können einige der Hypothesen $H_i$ aufgrund der Daten **verworfen** werden?
- Falls ja: wie sicher sind wir uns, dass das Verwerfen **korrekt** war?

In Hypothesentests mit mehr als einer Hypothese nimmt häufig eine der Hypothesen eine Sonderstellung ein, die **Nullhypothese** $H_0$. Sie entspricht oft dem aktuellen Wissensstand und wird mit Alternativhypothesen, die neue Effekte berücksichtigen, verglichen.

>**Wichtig**: Statistische Testverfahren erlauben immer nur das **Verwerfen** einer oder mehrerer Hypothesen, eine Hypothese kann nie **bewiesen** werden! Es könnte immer bessere Alternativen geben, die nicht getestet wurden.

Ein Hypothesentest läuft in vier Schritten ab:
1. Definition einer **Prüfgröße** zur Unterscheidung der Hypothesen
2. Festlegung von Kriterien zum **Verwerfen der Nullhypothese**
3. Messung der Prüfgröße
4. Entscheidung

Diese Schritte werden im folgenden genauer erläutert.

Ein **Beispiel** für einen Hypothesen aus der wissenschaftlichen Literatur ist die Frage nach dem Rauchen als Ursache von Lungenkrebs. Der folgende Datensatz stammt aus dem Bericht *Occupational Mortality: The Registrar General's Decennial Supplement for England and Wales, 1970-1972, Her Majesty's Stationery Office, London, 1978*. Er beinhaltet für 25 Personengruppen zwei Größen:
- Rauchindex: 100, wenn Zahl der Zigaretten pro Tag dem Durchschnitt von allen Männern desselben Alters entspricht.
- Lungenkrebsindex: 100, wenn Zahl der Lungenkrebstoten dem Durchschnitt entspricht.

Anhand dieser Daten werden in folgendem Codebeispiel zwei Hypothesen getestet. Hypothese $H_0$ besagt, dass kein Zusammenhang zwischen den beiden Größen besteht, Hypothese $H_1$, dass der Lungenkrebsindex mit dem Rauchindex ansteigt. Wir haben hier (willkürlich) "kein Zusammenhang" als Nullhypothese gewählt. Die Frage ist nun, ob $H_0$ anhand der Daten verworfen werden kann. Wenn wir die beiden Größen gegeneinander in einem Streudiagramm auftragen, entspricht $H_0$ einer horizontalen Gerade und $H_1$ einer Gerade mit positiver Steigung. In diesem Fall könnte der Korrelationskoeffizient als Größe zur Unterscheidung der Hypothesen (Prüfgröße, unten genauer eingeführt) herangezogen werden und die Frage gestellt werden, ob eine der Hypothesen aufgrund des Korrelationskoeffizients zurückgewiesen werden muss.

In [ ]:
"""Hypothesis testing: smoking as a cause for lung cancer?"""

import numpy as np
import matplotlib.pyplot as plt
from scipy.optimize import curve_fit

def H0_model( x, a0=1. ):
	return np.repeat( a0, len(x) ) # as x is ignored in this model, return a0 for every x value
	
def H1_model( x, a0=1., a1=1. ):
	'''Alternative hypothesis: straight line'''
	return a0 + a1*x

data = np.genfromtxt('data/smoking.csv', delimiter=",", skip_header=4 )
xdata, ydata = data[:,0], data[:,1]

fig,ax = plt.subplots()
ax.scatter( xdata, ydata, label="Data" )
ax.set_xlabel( "Smoking Index")
ax.set_ylabel( "Lung Cancer Index")
ax.text( 110, 52, "Correlation Coefficient: %5.3f" % np.corrcoef(data,rowvar=False)[0][1] )

xrange = np.linspace( 65, 145, 320 )

# Fit and plot H0 with scipy.optimize.curve_fit
popt, pcov = curve_fit( H0_model, xdata, ydata )
ax.plot( xrange, H0_model( xrange, *popt ), 'r', label="$H_0$" ) 

# Fit and plot H1 with scipy.optimize.curve_fit
popt, pcov = curve_fit( H1_model, xdata, ydata )
ax.plot( xrange, H1_model( xrange, *popt ), 'g', label="$H_1$" ) 

ax.legend()

plt.show()


#### Schritt 1 – Definition der Prüfgröße
In obigem Codebeispiel wurden die ursprügliche Stichprobe ("Rohdaten") bereits vorprozessiert: Individuen wurden in Personengruppen aufgeteilt und die Größen Rauchindex und Lungenkrebsindex sind so definiert, dass sie auf ihren Durchschnitt normiert sind. Die Hypothesen unterscheiden sich anhand der Steigung der Geraden im Streudiagramm dieser Größen oder im erwarteten Korrelationskoeffizienten. Beide sind Null für $H_0$ und verschieden von Null für $H_1$. Allgemein muss für einen Hypothesentest eine Funktion der Daten $\mathbf{x}=(x_1, \dots, x_n)^\mathsf{T}$ gefunden werden, anhand derer sich verschiedene Hypothesen **unterscheiden** lassen. Diese Größe wird als **Prüfgröße** $t(\mathbf{x})$ (engl.: test statistic) bezeichnet:
- $t(\mathbf{x})$ kann im Prinzip eine beliebige skalare Funktion der Daten sein. Ein Beispiel dafür ist die Likelihood-Funktion $L(H_i|\mathbf{x})$.
- $t(\mathbf{x})$ ist eine Zufallsvariable, die unter unterschiedlichen Hypothesen unterschiedlichen PDFs $g(t|H_i)$ folgt. Dies ist schematisch in folgenden Codebeispiel illustriert. Als PDF wurde (willkürlich, zu Illustrationszwecken) eine abschnittsweise definierte Funktion gewählt, eine Normalverteilung mit unterschiedlichen Skalierungsparameter links und rechts ihres Maximums.

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu:'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax = 0, 10
t = np.linspace( tmin, tmax, 200 )

fig,ax = plt.subplots()
ax.plot( t, double_gaussian_model( t, 3 ), label="$H_0$" )
ax.set_xlabel( "test statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

plt.show()

>**Bemerkung: Typen von Hypothesen** 
>
>Da Hypothesen in Hypothesentests als PDFs der Prüfgröße $g(t|H_i)$ formuliert werden, lassen sie sich anhand der Parameterabhängigkeit der Prüfgröße klassifizieren. Die PDFs, die die Hypothesen beschreiben, können von zwei Arten von Parametern abhängen: Die Parameter $\boldsymbol{\lambda}$ sind bereits vor dem Hypothesentest bekannt, und die Parameter $\boldsymbol{\theta}$ sind unbekannt und müssen aus den Daten bestimmt werden.
>- Als **einfache Hypothesen** werden Hypothesen bezeichnet, für die **alle Parameter der PDF bekannt** sind: $g(t|H_i(\boldsymbol{\lambda}))$. Beispiel: Daten in einem Zählexperiment folen einer Poissonverteilung mit bekanntem Parameter $\nu=5$.
>- Für **zusammengesetzte Hypothesen** ist die PDF bis auf einige Parameter $\boldsymbol{\theta}$ bekannt:  $g(t|H_i(\boldsymbol{\lambda},\boldsymbol{\theta}))$. Beispiel: Daten folgen einer Normalverteilung mit bekanntem Lokalisierungsparameter $\mu$ aber unbekanntem Skalierungsparameter $\sigma$, der aus Daten bestimmt werden muss.


>**Bemerkung: Wahl der Prüfgröße** 
>
>Eine geschickte Wahl der Prüfgröße ist wichtig, um einen möglichst aussagekräftigen Hypothesentest zu erhalten. Es gibt einen mathematischen Hilfssatz, das **Neyman-Pearson-Lemma**, das besagt, dass, falls für zwei einfache Hypothesen $H_0$ und $H_1$ die Likelihoodfunktionen $L(H_0)$ und $L(H_1)$ vollständig bekannt sind, der **Likelihood-Quotient** (engl.: likelihood ratio)
>$$
r(\mathbf{x}) = 
\frac{L(H_0|\mathbf{x})}{L(H_1|\mathbf{x})} =
\frac{\prod_{i=1}^n f(x_i|H_0)}{\prod_{i=1}^n f(x_i|H_1)}
>$$
> die **optimale Prüfgröße** ist. Das Problem mit der Anwendung des Neyman-Pearson-Lemmas in der Praxis ist, dass die Likelihood-Funktionen oft unbekannt sind. Daher werden anstatt dessen oft folgende Ansätze gewählt:
>- Plausibler **Ansatz** für funktionale Form der Prüfgröße
>- Näherung der Likelihood-Funktionen, z. B. durch aufwändige **Simulationen** mit der Monte-Carlo-Methode.
>- **Asympotische** Näherung im Grenzfall großer Stichproben (Stichwort: [Satz von Wilks](https://en.wikipedia.org/wiki/Wilks%27_theorem), engl.: Wilks' theorem, funktioniert auch für zusammengesetzte Hypothesen)
>
>Die Ableitung von statistischen Größen aus Daten, deren Likelihood nicht bekannt ist, ist ein aktuelles Forschungsfeld der künstlichen Intelligenz, das oft mit **Likelihood-free Inference** oder **Simulation-based Inference** bezeichnet wird.

#### Schritt 2 – Festlegung von Kriterien zum Verwerfen der Nullhypothese

Die Messung in folgenden Schritt 3 liefert einen Messwert $t=t_1$ für die Prüfgröße. Vor der Messung muss noch festgelegt werden, welchen Wert $t_0$ der Messwert mindestens annehmen muss, um die Nullhypothese zu verwerfen. Die Prüfgröße ist dabei (nach der üblichen Konvention) so gewählt, dass *größere* Werte von $t$ eine *schlechtere* Übereinstimmung mit der Nullhypothese implizieren. An der obigen Illustration ist abzulesen, dass viele PDFs $g(t|H_i)$ für alle $t\in\mathbb{R}$ von Null verschiedene Werte haben. Für jedes $t_0<\infty$, gibt es also eine endliche Wahrscheinlichkeit, dass die **Nullhypothese verworfen wird, obwohl sie wahr** ist. Diese Situation wird weiter unten als "Fehler erster Art" diskutiert, sie muss bei Hypothesentests praktisch immer inkauf genommen werden – eine **Hypothese kann nie mit hundertprozentiger Sicherheit verworfen werden**. Die maximal erlaubte Irrtumswahrscheinlichkeit $\alpha$  wird als **Signifikanzniveau** (engl.: significance level) bezeichnet, sie muss immer **vor der Messung festgelegt** werden. Mathematisch wird das wie folgt formuliert:
$$
\int_{t_0}^\infty g(t|H_0)\mathsf{d}t = \alpha.
$$
Es muss also ein Wert $t_0$ so gewählt werden, dass die Wahrscheinlichkeit dafür, dass $t_1\geq t_0$ gemessen wird, auch wenn die Nullhypothese wahr ist, gerade $\alpha$ entspricht. Das Codebeispiel weiter unten zeigt die geometrische Interpretation der Gleichung: gesucht ist ein Wert $t_0$, für den der Flächeninhalt unter der Kurve links von $t_0$ den Wert $\alpha$ annimmt.

#### Schritt 3 – Messung der Prüfgröße
Erst **nach** Festlegung des Signifikanzniveaus erfolgt die Messung der Prüfgröße; sie ergibt einen Wert $t=t_1$. Auch für diesen Wert berechnen wir die Wahrscheinlichkeit, dass $t\geq t_1$ gemessen wird, wenn die Nullhypothese wahr ist. Diese Größe wird als **p-Wert** (engl.: p value) bezeichnet:
$$
p = P(t\geq t_1|H_0)=\int_{t_1}^\infty g(t|H_0)\mathsf{d}t.
$$

>**Exkurs: Was ist ein p-Wert (und was nicht)?**
>
>Obwohl Signifikanzniveau und p-Wert über das gleiche Integral definiert sind, müssen sie genau unterschieden werden:
>- Das Signifikanzniveau $\alpha$ ist die  Wahrscheinlichkeit für einen Fehler erster Art, also die im Hypothesentest inkauf genommene Wahrscheinlichkeit, dass die Nullhypothese verworfen wird, obwohl sie wahr ist. Das Signifikanzniveau wird **vor der Messung festgelegt**.
>- Der p-Wert ist die Wahrscheinlichkeit, das ein Wert von $t\geq t_1$ gemessen wird, wenn die Nullhypothese wahr ist. Er steht erst fest, **nachdem $t_1$ gemessen wurde**.
>
>Im Zusammenhang mit dem p-Wert finden sich häufig Missverständnisse oder Ungenauigkeiten. Deswegen lohnt es sich, aufzulisten, was ein p-Wert unter anderem **nicht** ist:
>- Der p-Wert ist **nicht** die Wahrscheinlichkeit, dass die Nullhypothese wahr ist.
>- Der p-Wert ist **nicht** die Wahrscheinlichkeit, die Nullhypothese fälschlich zu verwerfen.
>- Der p-Wert ist **nicht** die Wahrscheinlichkeit, dass die Messung "nur eine Fluktuation" ist.
>
> **Der p-Wert ist die Wahrscheinlichkeit, dass ein Wert von $t\geq t_1$ gemessen wird, wenn die Nullhypothese wahr ist** – nicht mehr und nicht weniger!

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu:'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax, t0, t1 = 0, 10, 7, 5.2
t = np.linspace( tmin, tmax, 500 )
g = double_gaussian_model( t, 3, 1, 2 )

fig,ax = plt.subplots()

# plot PDF
ax.plot( t, g, label="$H_0$" )
ax.set_xlabel( "test statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

# plot significance level
ax.vlines( t0, 0, 0.2, colors="green" )
ax.text( t0, -0.02, "$t_0$", color="green", ha="center" )
ax.fill_between( t[t>t0], 0, g[t>t0], facecolor="green", alpha=0.3 )
ax.annotate( r"$\alpha$", xy=(t0+0.25,0.02), xytext=(t0+1,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

# plot measurement
ax.vlines( t1, 0, 0.2, colors="red" )
ax.text( t1, -0.02, "$t_1$", color="red", ha="center" )

plt.show()

#### Schritt 4: Entscheidung
Die Entscheidung erfolgt nun aufgrund eines Vergleichs des p-Werts für den Messwert $t_1$ der Prüfgröße mit dem vor der Messung festgelegten Signifikanzniveau:
- Die Hypothese $H_0$ wird **verworfen**, wenn der **p-Wert unterhalb des Signifikanzniveaus** liegt: $p<\alpha$. Dies entspricht $t_1>t_0$. Er besitzt dann immer noch eine (kleine aber endliche) Wahrscheinlichkeit wahr zu sein.
- Wenn der **p-Wert oberhalb des Signifikanzniveaus** liegt, also $p\geq\alpha$ bzw. $t_1\leq t_0$, dann kann die Hypothese $H_0$ **nicht verworfen** werden, obwohl sie eine (endliche aber kleine) Wahrscheinlichkeit besitzt, dass sie falsch ist.

#### Vergleich von Hypothesen
Der nächste Schritt beim Test von Hypothesen ist der Vergleich einer alternativen Hypothese $H_1$ mit der Nullhypothese $H_0$. Dabei stellt sich die Frage, wie gut die Hypothesen bei gegebenem Signifikanzniveau $\alpha$ unterschieden werden können. Das unten stehende Codebeispiel zeigt neben der PDF der Nullhypothese $g(t|H_0)$ auch die der alternativen Hypothese $g(t|H_1)$. Die dort eingezeichnete rote Fläche
$$
\beta = \int_{-\infty}^{t_0} g(t|H_1)\mathsf{d}t
$$
entspricht der Wahrscheinlichkeit, die Nullhypothese nicht zu verwerfen, selbst wenn die Alternativhypothese wahr ist. Dies wird als "Fehler zweiter Art" bezeichnet und wird weiter unten kurz diskutiert.

In [ ]:
"""Illustration of hypothesis testing"""
import numpy as np
import matplotlib.pyplot as plt 
from scipy.stats import norm
from scipy.integrate import quad

def double_gaussian_model( x, mu=0., sigma1=1., sigma2=2. ):
	'''Normal distributions with different sigmas left and right of mu'''
	fac=2./(sigma1+sigma2)
	return np.where( x < mu, fac*sigma1*norm.pdf( x, loc=mu, scale=sigma1), fac*sigma2*norm.pdf( x, loc=mu, scale=sigma2) )

# range of values
tmin, tmax, t0, t1 = 0, 10, 7, 5.2
t = np.linspace( tmin, tmax, 500 )
g0 = double_gaussian_model( t, 3, 1, 2 )
g1 = double_gaussian_model( t, 8.5, 1.5, 1)

fig,ax = plt.subplots()

# plot PDFs
ax.plot( t, g0, label="$H_0$" )
ax.plot( t, g1, label="$H_1$" )
ax.set_xlabel( "Test Statistic $t$" )
ax.set_ylabel( "$g(t|H_i)$")
ax.set_ylim( 0, 0.4 )
ax.legend()

# plot significance level alpha
ax.vlines( t0, 0, 0.3, colors="green" )
ax.text( t0, -0.025, "$t_0$", color="green", ha="center" )
ax.fill_between( t[t>t0], 0, g0[t>t0], facecolor="green", alpha=0.3 )
ax.annotate( r"$\alpha$", xy=(t0+0.25,0.02), xytext=(t0+1,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

# plot test power beta
ax.fill_between( t[t<t0], 0, g1[t<t0], facecolor="red", alpha=0.3 )
ax.annotate( r"$\beta$", xy=(t0-1.5,0.02), xytext=(t0-2.5,0.07), arrowprops=dict(facecolor="black", width=1, headwidth=5) )

plt.show()

Der Wert $1-\beta$ wird als **Teststärke** (auch: Trennschärfe, Mächtigkeit des Tests, engl.: power) bezeichnet. Er gibt an, mit welcher Wahrscheinlichkeit der Wert der Prüfgröße $t>t_0$ liegt, wenn die alternative Hypothese $H_1$ wahr ist. Da mit $t_0$ ja das Signifikanzniveau $\alpha$ festliegt, ist $1-\beta$ ein Maß dafür, wie gut sich die Hypothesen unterscheiden. Die Teststärke ist also umso größer, umso weniger Überlapp die beiden PDFs besitzen. Eine gute Prüfgröße sollte diesen Überlapp so gut wie möglich minimieren.

>**Exkurs: Fehlertypen**
>
> Die in diesem Abschnitt erwähnten Fehlertypen sollen hier noch einmal zusammengefasst werden. Es ist wichtig zu beachten, dass Hypothesentests (wie alle wissenschaftlichen Aussagen) **nie absolut sichere Resultate liefern** – Fehler müssen immer in Kauf genommen werden! 
>
>Ein **Fehler erster Art** (engl.: type-I error, false positive) wird dann begangen, wenn die **Nullhypothese verworfen wird, selbst wenn sie wahr ist**. In Hypothesentests wird die Wahrscheinlichkeit $\alpha$ für Fehler erster Art **vor** der Messung festgelegt. Beispiele für Fehler erster Art sind:
>- Eine Krankheit wird fälschlich bei gesunden Patient:innen diagnostiziert.
>- Ein neues Elementarteilchen wird fälschlicherweise entdeckt. Das dafür in der Physik übliche Signifikanzniveau beträgt $\alpha=3\times 10^{-7}$.
>- Ehrliche Kundschaft wird als Betrüger:in eingestuft.
>
>Ein **Fehler zweiter Art** (engl.: type-II error, false negative) wird begangen, wenn die **Nullhypothese nicht verworfen wird, selbst wenn sie falsch ist**. In Hypothesentests mit einer Alternativhypothese wird die Wahrscheinlichkeit $\beta$ für Fehler zweiter Art implizit durch $\alpha$ vor der Messung festgelegt. Beispiele für Fehler zweiter Art umfassen:
>- Eine Krankheit wird bei kranken Patient:innen nicht diagnostiziert.
>- Ein neues Elementarteilchen wird in Daten nicht entdeckt, obwohl es vorhanden ist. Hierfür ist ein Signifikanzniveau von $\alpha=5\%$ oder $\alpha=10\%$ üblich.
>- Ein Betrug wird nicht erkannt.

### Statistische Klassifizierung
Während bei Hypothesentests oft die Nullhypothese die Rolle einer ausgezeichneten Hypothese übernimmt, geht es bei der statistischen Klassifizierung (engl.: statistical classification) um den **Vergleich mehrerer gleichwertiger Hypothesen**. Das Ziel dabei ist es, Daten nach ihrem Merkmalen (engl.: features) in zwei oder mehr Klassen einzuteilen. Dazu muss ein **Klassifikator** (engl.: classifier) gefunden werden, der die bestmögiche Trennschärfe zwischen den Klassen bietet. Die Merkmale selbst und jede Funktion der Merkmale sind als Klassifikatoren grundsätzlich geeignet. In Daten könnte z. B. nach einer Unterscheidung zwischen Signal und Untergrund gesucht werden. Damit werden die Daten in zwei Klassen eingeteilt, dies wird auch als binäre Klassifikation (engl.: binary classification) bezeichnet. In der Bilderkennung sind oft mehrere Klassen gefragt, z. B. zur Unterscheidung von Hunden, Katzen, Mäusen, Autos usw. Diese Art der Klassifizierung heißt Multiklassen-Klassifizierung (engl.: multiclass classification) oder kurz Multiklassifizierung.

Der folgende Code zeigt eine binäre Klassifizierung zwischen Signal (rot) und Untergrund (blau) aufgrund von zwei Merkmalen. In diesem Fall kann durch "scharfes Hinsehen" ein linearer Klassifikator geraten werden: eine diagonale Gerade trennt die beiden Klassen, sie entspricht einer Linearkombination der beiden Merkmale.

In [ ]:
"""Example of binary classifications: two fuzzy rings"""

import numpy as np
import matplotlib.pyplot as plt 

rng = np.random.default_rng( 42 )

def random_ring( center=[0,0], radius=1, width=0.2, N=100 ):
    """generate random numbers: radius from normal distribution, uniform polar angle,
    return array of x and y from coordinate transformation, shifted by center"""
    r   = rng.normal( loc=radius, scale=width, size=N )
    phi = rng.uniform( 0, 2*np.pi, size=N )
    return [ center[0]+r*np.cos(phi), center[1]+r*np.sin(phi) ]

# create synthetic data: two intersecting rings
N = 200
ring1 = random_ring( [1,1], 2, 0.2, N )
ring2 = random_ring( [-1,-1], 2, 0.5, N )

fig,ax = plt.subplots()
ax.scatter( ring1[0], ring1[1], color="r", label="Signal" )
ax.scatter( ring2[0], ring2[1], color="b", label="Background" )

# create by-eye classifier
xl = np.linspace( -3, 3, 300 )
ax.plot( xl, -xl, color="green", linewidth=2, label="Classifier" )
ax.set_xlabel("Feature 1")
ax.set_ylabel("Feature 2")
ax.legend()

plt.show()


>**Bemerkung: Lineare Klassifizierung** 
>
>Anstatt die obige Klassifikation "mit Auge" durchzuführen, gibt es ein mathematisches Verfahren einen linearen Klassifikator zu finden, das von Ronald Aylmer Fisher im Jahr 1936  entwickelt wurde, und das zur **Fisher-Diskriminante** führt, die in vielen Lehrbüchern der statistischen Datenanalyse beschrieben wird, siehe z. B. [Wikipedia-Artikel zur Diskriminanzfunktion](https://de.wikipedia.org/wiki/Diskriminanzfunktion).


### Maschinelles Lernen
Eine lineare Klassifizierung hat ihre Grenzen: es kann gezeigt werden, dass sie nur für lineare Klassifikationsprobleme optimal funktioniert. Es gibt eine Reihe von nichtlinearen Klassifizierungsverfahren, von denen viele heute auf **maschinelles Lernen** (engl.: machine learning, ML) zurückgreifen. Im maschinellen Lernen findet ein Lernprozess statt, der oft auch **Training** genannt wird. Der Klassifikator besitzt dafür trainierbare Parameter, die innerhalb des Lernprozesses optimiert werden. Dazu werden dem Klassifikator Daten mit bekannter wahrer Klassifikation (engl.: labeled data) als Eingabegrößen zur Verfügung gestellt. Folgende Arten des maschinellen Lernens werden unterschieden:
- Derzeit ist das **überwachte Lernen** (engl.: supervised learning) die wichtigste Variante des maschinellen Lernens. Dabei wird die Ausgabe des Klassifikators mit der bekannten Klassifikation der Trainingsdaten verglichen und die trainierbaren Parameter so optimiert, dass die Differenz zwischen Ausgabe des Klassifikators und wahrer Klassifikation minimiert wird. 
- Beim **unüberwachte Lernen** (engl.: unsupervised learning) wird der Kassifikator allein aufgrund der Muster der Eingabegrößen trainiert.
- Das **bestärkende Lernen** (engl.: reinforcement learning) wird eine richtige Klassifikation "belohnt". 

Eine gute Online-Ressource für den Einstieg ins maschinelle Lernen ist das E-Buch [Deep Learning](http://deeplearningbook.org) von Ian Goodfellow, Yoshua Bengio und Aaron Courville.

>**MNIST-Datensatz**
>
> Im Forschungsfeld des mschinellen Lernens gibt es einige Standarddatensätze, die für den Vergleich von Klassifizierungsmethoden eingesetzt werden. Einer davon ist eine modifizerte Version einer Datenbank von handgeschriebenen Ziffern des National Institute of Standards and Technology NIST (Modified NIST, MNIST), dem US-amerikanischen Pendant zur deutschen Physikalisch-Technischen Bundesanstalt PTB. Die automatische Erkennung dieser Ziffern diente in Zeiten handaddressierter Briefe z. B dazu die Postleitzahlen automatisch auszulesen. Der Datensatz zum Training einer KI besteht aus 60.000 Bildern, zusätzlich gibt es 10.000 weitere Bilder für einen unabhängigen Test der KI; jedes Bild ist eine Matrix von $28\times 28$ Pixeln mit 255 Graustufen mit **bekannter** Klassifizierung. Die Aufgabe ist eine Multiklassen-Klassifizierung mit zehn Klassen, den Ziffern von 0 bis 9. Eine zufällige Auswahl dieser Bilder ist hier gezeigt.
>
><img src="img/mnist.png" width=60%>

#### Neuronale Netze
In der Literatur findet sich eine Vielzahl von von nichtlinearen Klassifikatoren, und in unterschiedlichen Wissenschaftsfeldern sind unterschiedliche Klassifikatoren gebräuchlich. In der Teilchenphysik waren bespielsweise seit Anfang der 2000er Jahre **verstärkte Entscheidungsbäume** (engl.: boosted decision trees) und künstliche **neuronale Netze** (engl.: artificial neural networks, NN) die gängigsten Klassifikatoren. Durch den anhaltenden Trend des "tiefen Lernens" (engl.: deep learning) spielen im Bereich des maschinellen Lernens heute Varianten von tiefen neuronalen Netzen die weitaus wichtigste Rolle, von der Bilderkennung mit Convolutional Neural Networks (CNNs) bis zu Large Language Models (LLMs) wie bei ChatGPT.

Neuronale Netze haben das menschliche Gehirn als Vorbild. Schematisch besteht ein Neuron aus Dendriten, die es mit Eingangsdaten versorgen, der Synapse, die diese Daten zusammenführt und wichtet, und dem Axon, das die gewichtete Summe der Signale mit einer Schwelle (engl.: threshold) vergleicht und entscheidet, ob daraus ein Ausgangssignal entsteht. Die Ausgabe eines Neurons ist also eine nichtlineare Funktion der Eingangsdaten, die an andere Neuronen weitergeleitet werden kann. Dies ist in folgender Abbildung illustriert:

<img src="img/neuron_brain.png" width=50%>

Ein einfaches Beispiel für ein künstliches neuronales Netz ist das **vorwärtsgerichtete NN** (engl.: feed-forward NN). Dieses NN besteht aus mehreren Lagen von Neuronen (in diesem Zusammenhang auch "Knoten" genannt). Die Lagen umfassen:
- **Eingangslage** (engl.: input layer), mit $n$ Knoten, die somit $n$ Merkmale verarbeiten können, 
- eine oder mehr **verdeckten Lagen** (eng.: hidden layers), üblicherweise mit mehr als $n$ Knoten,
- **Ausgangslage** (engl.: output layer), mit einem Knoten (binäre Klassifikation oder mehreren Knoten (Multiklassifikation).

In diesem NN-Typ ist jedes Neuron in einer Lage mit *allen* Neuronen der darauffolgenden Lage (und keinen weiteren Neuronen) verbunden (engl.: fully-connected layers, dense layers), wie in folgender Abbildung gezeigt:

<img src="img/multi_layer_perceptron.png" width=80%>

In vorwärtsgerichteten NN werden Daten also immer von Lage zu Lage "vorwärts" geleitet (von links nach rechts in obiger Abbildung), daher der Name. Das Training optimiert die Stärke aller Verbindungen zwischen Neuronen, ausgedrückt durch Gewichte. Die Größe $w_{ij}^{(k)}$ ist dabei das Gewicht zwischen Neuron $i$ der $k-1$-ten Lage und Neuron $j$ der $k$-ten Lage.
Dazu wird die Ausgabe des NN mit der wahren Klassifizierung anhand einer geeigneten **Verlustfunktion** (engl.: loss function) verglichen und die Gewichte so optimiert, dass die Verlustfunktion minimiert wird. Dabei kommen moderne Algorithmen der numerischen Optimierung zum Einsatz.

#### Beispiel: MNIST-Datensatz mit Keras
Die derzeit führenden Pakete für maschinelles Lernen in Python sind [`TensorFlow`](https://www.tensorflow.org) und [`PyTorch`](https://pytorch.org). Das folgende Beispiel nutzt TensorFlow über das Frontend [`Keras`](https://keras.io), das die Bedienung der TensorFlow-Funktionalität sehr vereinfacht. Zum Ausführen des unten stehende Beispiels müssen TensorFlow und Keras auf dem Rechner oder Server installliert sein, auf dem das Jupyter-Notebook ausgeführt wird. Auf dem Jupyter-Server [bwJupyter](https://hub.bwjupyter.de) funktioniert das derzeit mit dem Server `Jupyter TensorFlow`. Auf Ihrem eigenen Rechner können sie die Pakete mit `pip install tensorflow` oder in Anaconda mit `conda create -n tf tensorflow; conda activate tf` nachinstallieren.

Das folgende Codebeispiel legt zunächst die Hyperparameter des Modells fest, läd dann die MNIST-Bilder und stellt eine Auswahl grafisch dar. Dann wird das Modell definiert und Minimierungsalgorithmus (Adam, vgl. Abschnitt zur numerischen Optimierung) und Verlustfunktion (kategorische Kreuzentropie) festgelegt. Schließlich wird das Modell trainiert und die Genauigkeit der Klassifizierung, d. h. der Anteil der korrekt klassifizierten Bilder, ausgegeben. Probieren Sie gern andere NN-Architekturen und Hyperparameter aus.

In [ ]:
"""Statistical classification: NN from Keras/TensorFlow classifying MNIST dataset"""
from tensorflow.keras.datasets import mnist
from tensorflow.keras.models import Sequential
from tensorflow.keras.layers import Dense
from tensorflow.keras.utils import plot_model, to_categorical
import numpy as np
import matplotlib.pyplot as plt

# hyperparameters of Keras model
batchsize = 100
nclasses  = 10
epochs    = 20
dropout   = 0.2

In [ ]:
# MNIST dataset: 60000 (train) + 10000 (test) images (28x28 pixels, 8 bit grayscale)
datasize  = 28*28
( x_tr, y_tr ), ( x_te, y_te ) = mnist.load_data()

# show a matrix of random images
N = 15
rng = np.random.default_rng( 42 )
pics=rng.integers( 0, len(x_tr), N*N )

fig,ax = plt.subplots(N,N)
for a, i in zip( ax.reshape(-1), pics ):
    a.set_axis_off()
    a.imshow( x_tr[i] )
plt.savefig( "mnist.pdf" )

# NNs require feature *vectors* as inputs, therefore re-format the images (28x28) as vectors with 784 entries
x_tr = x_tr.reshape( 60000, datasize )

# scale the 255 shades of gray (8-bit integer) to float between 0 and 1
x_tr = x_tr.astype( 'float32' )
x_tr /= 255

# translate 10 categories (numbers 0..9) as matrix for Keras
y_tr = to_categorical( y_tr, nclasses )

# same processing for test data
x_te = x_te.reshape( 10000, datasize )
x_te = x_te.astype( 'float32' )
x_te /= 255
y_te = to_categorical( y_te, nclasses )

In [ ]:
# construct the model: feed-forward network with 1-3 hidden layers
model = Sequential()
model.add( Dense( 100, activation = 'relu', input_shape = ( datasize, ) ) )
#model.add( Dense( 100, activation = 'relu' ) )
#model.add( Dense( 100, activation = 'relu' ) )
model.add( Dense( nclasses, activation = 'softmax' ) )
model.summary()

# build model with ADAM optimizer and categorical cross-entropy as loss function
model.compile( optimizer = 'adam',
                loss = 'categorical_crossentropy',
                metrics = [ 'accuracy' ] )

In [ ]:
# train the model
history = model.fit( x_tr, y_tr,
                    epochs = epochs,
                    batch_size = batchsize,
                    verbose = 1,
                    validation_data = ( x_te, y_te ) )

# evaluate the previously trained model on test dataset
score = model.evaluate( x_te, y_te, verbose = 0 )
print( "loss function value after training:", score[0] )
print( "fraction of correctly classified images (accuracy):", score[1] )

#### Beispiel: MNIST-Datensatz mit PyTorch

In den letzten Jahren hat die Beliebtheit des Pakets [`PyTorch`](https://pytorch.org) für Aufgaben des maschinellen Lernens zugenommen. Deswegen folgt im folgenden eine Implementation des MNIST-Beispiels in PyTorch, die mithilfe von Chat-GPT generiert wurde. Im Vergleich zu Keras sind in PyTorch die einzelnen Schritte beim Training transparenter sichtbar.

Aufgrund der Größe der PyTorch-Pakete und den PyTorch-Abhängigkeiten von bestimmten Versionen von Python-Paketen bietet sich auch eine Installation mit `pip` in einer virtuellen Umgebung an. Dazu wechseln wir in ein beliebiges Arbeitsverzeichnis und installieren, falls noch nicht vorhanden, das Paket `virtualenv` mit dem Befehl 

`python -m pip install --user virtualenv`. 

Dann erzeugen wir die virtuelle Umgebung für PyTorch mit 

`python -m virtualenv pytorch` 

und aktivieren sie, z. B. in Linux oder MacOS mit 

`source pytorch/bin/activate`. 

Nun können wir innerhalb der virtuellen Umgebung PyTorch installieren: 

`pip install torch torchvision`.

Diese Installation kann danach jederzeit wieder aktiviert und verwendet werden.

In [ ]:
"""ChatGPT-generated code example for pytorch"""
import torch
import torch.nn as nn
import torch.optim as optim
import torchvision
import torchvision.transforms as transforms
from torch.utils.data import DataLoader
import time

# Check device (using Metal on Apple Silicon instead of CUDA on NVIDIA GPUs)
#device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
#device = torch.device("mps" if torch.backends.mps.is_available() else "cpu")
device="cpu"
print( "Processing device: ", device)

In [ ]:
# 1. Load and preprocess the MNIST dataset
transform = transforms.Compose([
    transforms.ToTensor(),  # Convert images to tensors
    transforms.Normalize((0.1307,), (0.3081,))  # Normalize with mean and std of MNIST
])

train_dataset = torchvision.datasets.MNIST(root='./data', train=True, download=True, transform=transform)
test_dataset = torchvision.datasets.MNIST(root='./data', train=False, download=True, transform=transform)

train_loader = DataLoader(train_dataset, batch_size=64, shuffle=True)
test_loader = DataLoader(test_dataset, batch_size=1000, shuffle=False)

In [ ]:
# 2. Define a simple neural network
class Net(nn.Module):
    def __init__(self):
        super(Net, self).__init__()
        self.fc1 = nn.Linear(28*28, 128)
        self.relu1 = nn.ReLU()
        self.fc2 = nn.Linear(128, 64)
        self.relu2 = nn.ReLU()
        self.fc3 = nn.Linear(64, 10)

    def forward(self, x):
        x = x.view(-1, 28*28)  # Flatten the image
        x = self.relu1(self.fc1(x))
        x = self.relu2(self.fc2(x))
        return self.fc3(x)

model = Net().to(device)

# 3. Define loss function and optimizer
criterion = nn.CrossEntropyLoss()
optimizer = optim.Adam(model.parameters(), lr=0.001)

In [ ]:
# 4. Training loop
start = time.time()
for epoch in range(5):  # Train for 5 epochs
    model.train()
    total_loss = 0
    for images, labels in train_loader:
        images, labels = images.to(device), labels.to(device)

        # Forward pass
        outputs = model(images)
        loss = criterion(outputs, labels)

        # Backward and optimize
        optimizer.zero_grad()
        loss.backward()
        optimizer.step()
        total_loss += loss.item()

    print(f"Epoch [{epoch+1}/5], Loss: {total_loss:.4f}")
end = time.time()
print(f"Training duration on {device}: {end-start:.4f} seconds")

# 5. Evaluation
model.eval()
correct = 0
total = 0
with torch.no_grad():
    for images, labels in test_loader:
        images, labels = images.to(device), labels.to(device)
        outputs = model(images)
        _, predicted = torch.max(outputs.data, 1)
        total += labels.size(0)
        correct += (predicted == labels).sum().item()

print(f"Accuracy on test set: {100 * correct / total:.2f}%")

# Zum Schluss
Der Kurs **Computergestützte Datenauswertung** (CgDA) war Ihre erste Einführung in Umgang mit Daten am Computer im Physikstudium. Er stellt für das Studium eine wichtige **Schlüsselqualifikation** dar, besonders im Hinblick auf physikalische Praktika und Abschlussarbeiten. Er trägt darüber hinaus wesentlich zur Schlüsselqualifikation **Datenkompetenz** ("Data Literacy"). Vieles in der Computeranwendung in der Physik ist **"learning by doing"** – wie bei jedem Werkzeug lernen Sie den Umgang damit am besten durch regelmäßiges Bedienen. Die Unterlagen zur Vorlesung (Folien und Skript mit Beispielen, Übungsaufgaben) bieten Ihnen dafür eine gute Basis für den Rest Ihres Studiums. 

**Bleiben Sie am Ball – neugierige und kreative Köpfe sind gefragt!**
